## import & data

In [33]:
import pandas as pd
import numpy as np
import re
import folium
from folium.plugins import HeatMap
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut
import pandas as pd
import folium
import branca
from folium.plugins import HeatMap
from opencage.geocoder import OpenCageGeocode

In [34]:
pd_calls = pd.read_csv("prepared_pd_calls.csv")
pd_calls = pd_calls.drop(pd_calls.columns[0], axis=1)
pd_calls.head()

Incident_Number          CreateDatetime                    Call_Type  \
0   2023-00062204  2023/12/29 20:27:46+00        CFS 1182 - Non Injury   
1   2023-00062206  2023/12/29 20:26:14+00     CFS 1042 - Welfare Check   
2   2023-00062200  2023/12/29 20:12:38+00   CFS FOUND - Found Property   
3   2023-00062228  2023/12/29 20:05:59+00  CFS 20002 - Hit & Run Prop.   
4   2023-00062202  2023/12/29 19:45:10+00        CFS 415 - Disturbance   

  Priority                  Block_Address  intersection add_num       street  
0  Level 3  SHATTUCK AVE  &  CHANNING WAY          True       0            0  
1  Level 2                 2400 ASHBY AVE         False    2400    ASHBY AVE  
2  Level 4                    700 PAGE ST         False     700      PAGE ST  
3  Level 3                1800 SOLANO AVE         False    1800   SOLANO AVE  
4  Level 2               1300 DELAWARE ST         False    1300  DELAWARE ST

In [35]:
pd_calls['street1'] = pd_calls.apply(lambda row: row['Block_Address'].split(' & ')[0] if row['intersection'] else None, axis=1)
pd_calls['street2'] = pd_calls.apply(lambda row: row['Block_Address'].split(' & ')[1] if row['intersection'] and len(row['Block_Address'].split(' & ')) > 1 else None, axis=1)
pd_calls

Incident_Number          CreateDatetime                    Call_Type  \
0       2023-00062204  2023/12/29 20:27:46+00        CFS 1182 - Non Injury   
1       2023-00062206  2023/12/29 20:26:14+00     CFS 1042 - Welfare Check   
2       2023-00062200  2023/12/29 20:12:38+00   CFS FOUND - Found Property   
3       2023-00062228  2023/12/29 20:05:59+00  CFS 20002 - Hit & Run Prop.   
4       2023-00062202  2023/12/29 19:45:10+00        CFS 415 - Disturbance   
...               ...                     ...                          ...   
53152   2022-00060808  2022/12/31 00:27:58+00        CFS 415 - Disturbance   
53153   2022-00060803  2022/12/31 00:16:42+00     CFS A911 - Ascertain 911   
53154   2022-00060799  2022/12/31 00:15:26+00     CFS A911 - Ascertain 911   
53155   2023-00090006  2022/12/31 00:13:27+00        CFS 487 - Grand Theft   
53156   2022-00060821  2022/12/31 00:05:57+00          CFS ADVICE - Advice   

      Priority                   Block_Address  intersection add_num  \
0      Level 3   SHATTUCK AVE  &  CHANNING WAY          True       0   
1      Level 2                  2400 ASHBY AVE         False    2400   
2      Level 4                     700 PAGE ST         False     700   
3      Level 3                 1800 SOLANO AVE         False    1800   
4      Level 2                1300 DELAWARE ST         False    1300   
...        ...                             ...           ...     ...   
53152  Level 4               2000 BERKELEY WAY         False    2000   
53153  Level 1                  2500 MILVIA ST         False    2500   
53154  Level 1                 1800 SOLANO AVE         False    1800   
53155   Level                  2600 DWIGHT WAY         False    2600   
53156  Level 4  2100 MARTIN LUTHER KING JR WAY         False    2100   

                          street        street1        street2  
0                              0  SHATTUCK AVE    CHANNING WAY  
1                      ASHBY AVE           None           None  
2                        PAGE ST           None           None  
3                     SOLANO AVE           None           None  
4                    DELAWARE ST           None           None  
...                          ...            ...            ...  
53152               BERKELEY WAY           None           None  
53153                  MILVIA ST           None           None  
53154                 SOLANO AVE           None           None  
53155                 DWIGHT WAY           None           None  
53156  MARTIN LUTHER KING JR WAY           None           None  

[53157 rows x 10 columns]

In [38]:
pd_calls["street"].unique()

array(['0', 'ASHBY AVE', 'PAGE ST', 'SOLANO AVE', 'DELAWARE ST', '9TH ST',
       'ALCATRAZ AVE', 'MARTIN LUTHER KING JR WAY', 'FRANCISCO ST',
       'SONOMA AVE', 'TELEGRAPH AVE', 'HEARST AVE', 'UNIVERSITY AVE',
       'RUSSELL ST', 'SAN PABLO AVE', '5TH ST', 'HILGARD AVE',
       'MARINA BLVD', 'SHATTUCK AVE', 'GRANT ST', 'CURTIS ST', '4TH ST',
       'EASTSHORE HWY', 'MARIN AVE', 'DURANT AVE', 'CALIFORNIA ST',
       'BENVENUE AVE', '6TH ST', 'WARD ST', 'KITTREDGE ST',
       'ARLINGTON AVE', 'PARK ST', 'SACRAMENTO ST', 'BOLIVAR DR',
       'HARPER ST', 'ACTON ST', 'CRAGMONT AVE', 'BERKELEY WAY',
       'ALLSTON WAY', 'COLLEGE AVE', 'FAIRVIEW ST', 'ADELINE ST',
       'DWIGHT WAY', 'BONITA AVE', 'SPAULDING AVE', 'DOHR ST',
       'ADDISON ST', 'BANCROFT WAY', 'BONAR ST', '8TH ST', 'PROSPECT ST',
       'CEDAR ST', 'MILVIA ST', 'IDAHO ST', 'WALNUT ST', 'PRINCE ST',
       'HARMON ST', 'NORTHAMPTON AVE', 'EUCLID AVE', 'BLAKE ST',
       'REGAL RD', '7TH ST', 'PARKER ST', 'CRESTON RD',

In [39]:
number_to_word = {
    '9THST': 'NINETHST',
    '4THST': 'FOURTHST',
    '6THST': 'SIXTHST',
    '7THST': 'SEVENTHST',
    '5THST': 'FIFTHST',
    '8THST': 'EIGHTHST',
    '2NDST': 'SECONDST',
    '67THST': 'SIXTYSEVENTHST',
    '10THST': 'TENTHST',
    '66THST': 'SIXTYSIXTHST',
    '63RDST': 'SIXTYTHIRDST',
    '62NDST': 'SIXTYSECONDST'
}

In [40]:
def remove_street(text):
    if text == '0':
        return 'INT'
    if not isinstance(text, str):
        text = str(text)
    text = text.replace(" ", "").upper()  
    
    for number, word in number_to_word.items():
        text = text.replace(number, word)
    text = re.sub(r'[^a-zA-Z]', '', text)
    pattern = re.compile(r'(AVE|ST|CT|RD|WAY|DR|HWY|PL|CIR|CRES)[^A-Za-z]*')
    matches = list(pattern.finditer(text))
    if matches:
        last_match = matches[-1]
        return text[:last_match.end(1)]
    return text

In [45]:
pd_calls['street'] = pd_calls['street'].apply(remove_street)
pd_calls['street1'] = pd_calls['street1'].apply(remove_street)
pd_calls['street2'] = pd_calls['street2'].apply(remove_street)

In [46]:
pd_calls["street"].unique()

array(['INT', 'ASHBYAVE', 'PAGEST', 'SOLANOAVE', 'DELAWAREST', 'NINETHST',
       'ALCATRAZAVE', 'MARTINLUTHERKINGJRWAY', 'FRANCISCOST', 'SONOMAAVE',
       'TELEGRAPHAVE', 'HEARSTAVE', 'UNIVERSITYAVE', 'RUSSELLST',
       'SANPABLOAVE', 'FIFTHST', 'HILGARDAVE', 'MARINABLVD',
       'SHATTUCKAVE', 'GRANTST', 'CURTISST', 'FOURTHST', 'EASTSHOREHWY',
       'MARINAVE', 'DURANTAVE', 'CALIFORNIAST', 'BENVENUEAVE', 'SIXTHST',
       'WARDST', 'KITTREDGEST', 'ARLINGTONAVE', 'PARKST', 'SACRAMENTOST',
       'BOLIVARD', 'HARPERST', 'ACTONST', 'CRAGMONTAVE', 'BERKELEYWAY',
       'ALLSTONWAY', 'COLLEGEAVE', 'FAIRVIEWST', 'ADELINEST', 'DWIGHTWAY',
       'BONITAAVE', 'SPAULDINGAVE', 'DOHRST', 'ADDISONST', 'BANCROFTWAY',
       'BONARST', 'EIGHTHST', 'PROSPECTST', 'CEDARST', 'MILVIAST',
       'IDAHOST', 'WALNUTST', 'PRINCEST', 'HARMONST', 'NORTHAMPTONAVE',
       'EUCLIDAVE', 'BLAKEST', 'REGALRD', 'SEVENTHST', 'PARKERST',
       'CRESTONRD', 'JONESST', 'ELLSWORTHST', 'THEUPL', 'CENTERST',
       

In [49]:
pd_calls["street1"].unique()

array(['SHATTUCKAVE', 'NONE', 'SEVENTHST', 'EIGHTHST', 'ELLSWORTHST',
       'CRAGMONTAVE', 'ENSENADAAVE', 'ACTONST', 'NINETHST',
       'SACRAMENTOST', 'COLLEGEAVE', 'HEARSTAVE', 'ADELINEST', 'TENTHST',
       'REGENTST', 'ALCATRAZAVE', 'DWIGHTWAY', 'ADDISONST',
       'MARTINLUTHERKINGJRWAY', 'CALIFORNIAST', 'GILMANST', 'RIDGERD',
       'BANCROFTWAY', 'ROSEST', 'KALABAGAIWAY', 'VIRGINIAST', 'SOLANOAVE',
       'UNIVERSITYAVE', 'TELEGRAPHAVE', 'FIFTHST', 'OREGONST',
       'THEALAMEDA', 'ARLINGTONAVE', 'CEDARST', 'ASHBYAVE',
       'EASTSHOREHWY', 'SECONDST', 'FOURTHST', 'FAIRVIEWST', 'HARMONST',
       'DURANTAVE', 'HENRYST', 'MURRAYST', 'SANPABLOAVE', 'CENTERST',
       'BERKELEYWAY', 'SANBARBARA', 'MILVIAST', 'TREMONTST', 'BYRONST',
       'CHANNINGWAY', 'SIXTHST', 'COLUSAAVE', 'RUSSELLST',
       'WILDCATCANYONRD', 'LALOMAAVE', 'DELNORTEST', 'PRINCEST', 'VINEST',
       'CORNELLAVE', 'KITTREDGEST', 'ALLSTONWAY', 'KAINSAVE', 'ESSEXST',
       'PAGEST', 'OXFORDST', 'BUENAVISTAWAY',

In [68]:
business_streets = set(business['street'].unique())
filtered_pd_calls = pd_calls[
    (pd_calls['street'].isin(business_streets)) |
     (pd_calls['street1'].isin(business_streets)) |
    (pd_calls['street2'].isin(business_streets))
]
filtered_pd_calls = filtered_pd_calls.reset_index(drop=True)
filtered_pd_calls

Incident_Number          CreateDatetime                    Call_Type  \
0       2023-00062204  2023/12/29 20:27:46+00        CFS 1182 - Non Injury   
1       2023-00062206  2023/12/29 20:26:14+00     CFS 1042 - Welfare Check   
2       2023-00062200  2023/12/29 20:12:38+00   CFS FOUND - Found Property   
3       2023-00062228  2023/12/29 20:05:59+00  CFS 20002 - Hit & Run Prop.   
4       2023-00062202  2023/12/29 19:45:10+00        CFS 415 - Disturbance   
...               ...                     ...                          ...   
48512   2022-00060813  2022/12/31 00:32:18+00           CFS 459 - Burglary   
48513   2022-00060808  2022/12/31 00:27:58+00        CFS 415 - Disturbance   
48514   2022-00060803  2022/12/31 00:16:42+00     CFS A911 - Ascertain 911   
48515   2022-00060799  2022/12/31 00:15:26+00     CFS A911 - Ascertain 911   
48516   2023-00090006  2022/12/31 00:13:27+00        CFS 487 - Grand Theft   

      Priority                  Block_Address  intersection add_num  \
0      Level 3  SHATTUCK AVE  &  CHANNING WAY          True       0   
1      Level 2                 2400 ASHBY AVE         False    2400   
2      Level 4                    700 PAGE ST         False     700   
3      Level 3                1800 SOLANO AVE         False    1800   
4      Level 2               1300 DELAWARE ST         False    1300   
...        ...                            ...           ...     ...   
48512  Level 3                2200 DWIGHT WAY         False    2200   
48513  Level 4              2000 BERKELEY WAY         False    2000   
48514  Level 1                 2500 MILVIA ST         False    2500   
48515  Level 1                1800 SOLANO AVE         False    1800   
48516   Level                 2600 DWIGHT WAY         False    2600   

            street      street1      street2  
0              INT  SHATTUCKAVE  CHANNINGWAY  
1         ASHBYAVE         NONE         NONE  
2           PAGEST         NONE         NONE  
3        SOLANOAVE         NONE         NONE  
4       DELAWAREST         NONE         NONE  
...            ...          ...          ...  
48512    DWIGHTWAY         NONE         NONE  
48513  BERKELEYWAY         NONE         NONE  
48514     MILVIAST         NONE         NONE  
48515    SOLANOAVE         NONE         NONE  
48516    DWIGHTWAY         NONE         NONE  

[48517 rows x 10 columns]

In [54]:
business = pd.read_csv("business+alcohol.csv")
business = business.drop(business.columns[0], axis=1)
business.head()

BusDesc               B1_PER_SUB_TYPE  \
0                 CLOTHING STORE                  Retail Trade   
1                       CATERING                  Retail Trade   
2  CANNABIS DISPENSARY - MEDICAL                      Cannabis   
3                MASSAGE THERAPY                       Massage   
4              AUTOMOTIVE REPAIR  Business Personal Repair Svs   

                DBA                                  Business_Location  \
0       RADBIRD LLC  2938 DOMINGO AVE\nBERKELEY, CA 94705\n(37.8583...   
1    LA CREPE A MOI  2432 NINTH ST\nBERKELEY, CA 94710\n(37.8611980...   
2  THE APOTHECARIUM  2312 TELEGRAPH AVE\nBERKELEY, CA 94704\n(37.86...   
3        PAPEN GINA  2337 PARKER ST 12\nBERKELEY, CA 94704\n(37.863...   
4   AVS SPECIALISTS  2210 SAN PABLO AVE\nBERKELEY, CA 94702\n(37.86...   

                  add add_num        street         new_name  alcohol  
0    2938 DOMINGO AVE    2938    DOMINGOAVE       RADBIRDLLC    False  
1       2432 NINTH ST    2432       NINTHST      LACREPEAMOI    False  
2  2312 TELEGRAPH AVE    2312  TELEGRAPHAVE  THEAPOTHECARIUM    False  
3   2337 PARKER ST 12    2337      PARKERST        PAPENGINA    False  
4  2210 SAN PABLO AVE    2210   SANPABLOAVE   AVSSPECIALISTS    False

In [56]:
business["street"].unique()

array(['DOMINGOAVE', 'NINTHST', 'TELEGRAPHAVE', 'PARKERST', 'SANPABLOAVE',
       'ASHBYAVE', 'JOSEPHINEST', 'SHATTUCKAVE', 'DURANTAVE', 'GILMANST',
       'BERKELEY,CA', 'EIGHTHST', 'CENTERST', 'SIXTHST', 'FIFTHST',
       'STUARTST', 'BANCROFTWAY', 'HALCYONCT', 'HOPKINSST', 'FOURTHST',
       'SEVENTHST', 'HILGARDAVE', 'TUNNELRD', 'RIDGERDCDSP', 'EUCLIDAVE',
       'COLLEGEAVEA', 'UNIVERSITYAVE', 'REGENTST', 'PRINCEST',
       'VICENTERD', 'ROOSEVELTAVE', 'HEINZAVE', 'MLKINGJRWAY',
       'ALCATRAZAVE', 'BLAKEST', 'SEVENTHSTB', 'WALNUTSTA',
       'SACRAMENTOST', 'CARLETONST', 'CHANNINGWAY', 'SANPABLOAVEE',
       'ADDISONST', 'BONITAAVE', 'BROOKSIDEDR', 'OXFORDST', 'MCGEEAVE',
       'ALLSTONWAY', 'COLUSAAVE', 'DELAWAREST', 'SIERRAST', 'HEARSTAVE',
       'GRAYSONST', 'CALIFORNIAST', 'ADELINEST', 'OREGONST', 'WALNUTST',
       'LINCOLNST', 'KALABAGAIWAY', 'SHATTUCKAVEC', 'GRANTST',
       'VIRGINIAST', 'SOLANOAVE', 'ACACIAAVE', 'FRANCISCOST',
       'GREENWOODTER', 'FULTONST', 'DERB

In [58]:
def remove_non_alphabetic(text):
    return re.sub(r'[^a-zA-Z]', '', text)

def remove_ca(text):
    if text.endswith('CA'):
        return text[:-2]
    return text

def remove_after_street_abbr(text):
    text = text.upper() 
    pattern = re.compile(r'(AVE|ST|CT|RD|WAY|DR|HWY|PL|CIR|CRES)[^A-Za-z]*')
    matches = list(pattern.finditer(text))
    if matches:
        last_match = matches[-1]
        return text[:last_match.end(1)]
    return text

business['street'] = business['street'].apply(remove_non_alphabetic)
business['street'] = business['street'].apply(remove_ca)
business['street'] = business['street'].apply(remove_after_street_abbr)

In [60]:
business["street"].unique()

array(['DOMINGOAVE', 'NINTHST', 'TELEGRAPHAVE', 'PARKERST', 'SANPABLOAVE',
       'ASHBYAVE', 'JOSEPHINEST', 'SHATTUCKAVE', 'DURANTAVE', 'GILMANST',
       'BERKELEY', 'EIGHTHST', 'CENTERST', 'SIXTHST', 'FIFTHST',
       'STUARTST', 'BANCROFTWAY', 'HALCYONCT', 'HOPKINSST', 'FOURTHST',
       'SEVENTHST', 'HILGARDAVE', 'TUNNELRD', 'RIDGERD', 'EUCLIDAVE',
       'COLLEGEAVE', 'UNIVERSITYAVE', 'REGENTST', 'PRINCEST', 'VICENTERD',
       'ROOSEVELTAVE', 'HEINZAVE', 'MLKINGJRWAY', 'ALCATRAZAVE',
       'BLAKEST', 'WALNUTST', 'SACRAMENTOST', 'CARLETONST', 'CHANNINGWAY',
       'ADDISONST', 'BONITAAVE', 'BROOKSIDEDR', 'OXFORDST', 'MCGEEAVE',
       'ALLSTONWAY', 'COLUSAAVE', 'DELAWAREST', 'SIERRAST', 'HEARSTAVE',
       'GRAYSONST', 'CALIFORNIAST', 'ADELINEST', 'OREGONST', 'LINCOLNST',
       'KALABAGAIWAY', 'GRANTST', 'VIRGINIAST', 'SOLANOAVE', 'ACACIAAVE',
       'FRANCISCOST', 'GREENWOODTER', 'FULTONST', 'DERBYST',
       'VIRGINIAGARD', 'PIEDMONTAVE', 'BURNETTST', 'JONESST', 'TENTHST',
  

In [62]:
business.head()

BusDesc               B1_PER_SUB_TYPE  \
0                 CLOTHING STORE                  Retail Trade   
1                       CATERING                  Retail Trade   
2  CANNABIS DISPENSARY - MEDICAL                      Cannabis   
3                MASSAGE THERAPY                       Massage   
4              AUTOMOTIVE REPAIR  Business Personal Repair Svs   

                DBA                                  Business_Location  \
0       RADBIRD LLC  2938 DOMINGO AVE\nBERKELEY, CA 94705\n(37.8583...   
1    LA CREPE A MOI  2432 NINTH ST\nBERKELEY, CA 94710\n(37.8611980...   
2  THE APOTHECARIUM  2312 TELEGRAPH AVE\nBERKELEY, CA 94704\n(37.86...   
3        PAPEN GINA  2337 PARKER ST 12\nBERKELEY, CA 94704\n(37.863...   
4   AVS SPECIALISTS  2210 SAN PABLO AVE\nBERKELEY, CA 94702\n(37.86...   

                  add add_num        street         new_name  alcohol  
0    2938 DOMINGO AVE    2938    DOMINGOAVE       RADBIRDLLC    False  
1       2432 NINTH ST    2432       NINTHST      LACREPEAMOI    False  
2  2312 TELEGRAPH AVE    2312  TELEGRAPHAVE  THEAPOTHECARIUM    False  
3   2337 PARKER ST 12    2337      PARKERST        PAPENGINA    False  
4  2210 SAN PABLO AVE    2210   SANPABLOAVE   AVSSPECIALISTS    False

In [66]:
pd_streets = set(pd_calls['street'].unique())
business = business[
    (business['street'].isin(pd_streets))
]
business

BusDesc               B1_PER_SUB_TYPE  \
0                               CLOTHING STORE                  Retail Trade   
2                CANNABIS DISPENSARY - MEDICAL                      Cannabis   
3                              MASSAGE THERAPY                       Massage   
4                            AUTOMOTIVE REPAIR  Business Personal Repair Svs   
5                              SERVICE STATION                  Retail Trade   
...                                        ...                           ...   
8544                       RESTAURANT & MARKET                  Retail Trade   
8545             DESIGN & SELL COMPUTER BOARDS                  Retail Trade   
8546                           RENTAL PROPERTY       Rental of Real Property   
8547  CHIROPRACTIC SERVICES TO THE UNDERSERVED      Non Profit Organizations   
8548              RESIDENTIAL RENTALS  4 UNITS       Rental of Real Property   

                              DBA  \
0                     RADBIRD LLC   
2                THE APOTHECARIUM   
3                      PAPEN GINA   
4                 AVS SPECIALISTS   
5           BRIDGEWAY SERVICE INC   
...                           ...   
8544  PIADINA ORIGINAL MARINA LLC   
8545                   FURAXA INC   
8546                 LIAO CHI JUN   
8547  LOVEJUST COMMUNITY WELLNESS   
8548   WANG JOHN HELEN & CLIFFORD   

                                      Business_Location  \
0     2938 DOMINGO AVE\nBERKELEY, CA 94705\n(37.8583...   
2     2312 TELEGRAPH AVE\nBERKELEY, CA 94704\n(37.86...   
3     2337 PARKER ST 12\nBERKELEY, CA 94704\n(37.863...   
4     2210 SAN PABLO AVE\nBERKELEY, CA 94702\n(37.86...   
5     3009 ASHBY AVE\nBERKELEY, CA 94705\n(37.858295...   
...                                                 ...   
8544  2905 COLLEGE AVE\nBERKELEY, CA 94705\n(37.8581...   
8545  808 GILMAN ST\nBERKELEY, CA 94710\n(37.8788880...   
8546  2509 DANA ST\nBERKELEY, CA 94704\n(37.86444599...   
8547  2718 TELEGRAPH AVE 210\nBERKELEY, CA 94705\n(3...   
8548  2115 GRANT ST\nBERKELEY, CA 94703\n(37.8697379...   

                         add add_num        street                   new_name  \
0           2938 DOMINGO AVE    2938    DOMINGOAVE                 RADBIRDLLC   
2         2312 TELEGRAPH AVE    2312  TELEGRAPHAVE            THEAPOTHECARIUM   
3          2337 PARKER ST 12    2337      PARKERST                  PAPENGINA   
4         2210 SAN PABLO AVE    2210   SANPABLOAVE             AVSSPECIALISTS   
5             3009 ASHBY AVE    3009      ASHBYAVE           BRIDGEWAYSERVICE   
...                      ...     ...           ...                        ...   
8544        2905 COLLEGE AVE    2905    COLLEGEAVE   PIADINAORIGINALMARINALLC   
8545           808 GILMAN ST     808      GILMANST                     FURAXA   
8546            2509 DANA ST    2509        DANAST                 LIAOCHIJUN   
8547  2718 TELEGRAPH AVE 210    2718  TELEGRAPHAVE  LOVEJUSTCOMMUNITYWELLNESS   
8548           2115 GRANT ST    2115       GRANTST      WANGJOHNHELENCLIFFORD   

      alcohol  
0       False  
2       False  
3       False  
4       False  
5       False  
...       ...  
8544     True  
8545    False  
8546    False  
8547    False  
8548    False  

[8136 rows x 9 columns]

In [70]:
street_ranges = business.groupby('street')['add_num'].agg(lambda x: (x.min(), x.max())).reset_index()
street_ranges[['min', 'max']] = pd.DataFrame(street_ranges['add_num'].tolist(), index=street_ranges.index)
street_ranges = street_ranges.drop(columns=['add_num'])

alcohol_count = business[business['alcohol']].groupby('street').size().reset_index(name='alcohol_true_count')

top_busdesc = (business.groupby('street')['BusDesc']
               .agg(lambda x: x.value_counts().head(3).index.tolist())
               .reset_index(name='top_3_busdesc'))

top_b1_per_sub_type = (business.groupby('street')['B1_PER_SUB_TYPE']
                       .agg(lambda x: x.value_counts().head(3).index.tolist())
                       .reset_index(name='top_3_b1_per_sub_type'))

result = pd.merge(street_ranges, alcohol_count, on='street', how='left')
result = pd.merge(result, top_busdesc, on='street', how='left')
result = pd.merge(result, top_b1_per_sub_type, on='street', how='left')

result['alcohol_true_count'] = result['alcohol_true_count'].fillna(0)

result['top_3_busdesc'] = result['top_3_busdesc'].apply(lambda x: ', '.join(x))
result['top_3_b1_per_sub_type'] = result['top_3_b1_per_sub_type'].apply(lambda x: ', '.join(x))
result = result.drop(columns=['min', 'max'])
print(result)

           street  alcohol_true_count  \
0       ACACIAAVE                 0.0   
1       ACTONCRES                 0.0   
2         ACTONST                 0.0   
3           ADAST                 0.0   
4       ADDISONST                 4.0   
..            ...                 ...   
301   WOODMONTAVE                 0.0   
302     WOOLSEYST                 0.0   
303  WPARNASSUSCT                 0.0   
304       YOLOAVE                 0.0   
305    YOSEMITERD                 0.0   

                                         top_3_busdesc  \
0                          CONSULTATION - PSYCHOLOGIST   
1    PROJECT MANAGEMENT, REAL ESTATE DEVELOPMENT, Y...   
2    RESIDENTIAL RENTAL 4 UNITS, RESIDENTIAL RENTAL...   
3    TDM CONSULTING SERVICES, DOCUMENT SHREDDING, A...   
4       COMMERCIAL RENTAL PROPERTY, ATTORNEY, LAW FIRM   
..                                                 ...   
301     ARCHITECTURE & DESIGN, CONSULTANT, HEALTH CARE   
302  RESIDENTIAL RENTAL 3 UNITS, RESIDENTIA

In [72]:
merged_df = pd.merge(filtered_pd_calls, result, on='street', how='left')
merged_df

Incident_Number          CreateDatetime                    Call_Type  \
0       2023-00062204  2023/12/29 20:27:46+00        CFS 1182 - Non Injury   
1       2023-00062206  2023/12/29 20:26:14+00     CFS 1042 - Welfare Check   
2       2023-00062200  2023/12/29 20:12:38+00   CFS FOUND - Found Property   
3       2023-00062228  2023/12/29 20:05:59+00  CFS 20002 - Hit & Run Prop.   
4       2023-00062202  2023/12/29 19:45:10+00        CFS 415 - Disturbance   
...               ...                     ...                          ...   
48512   2022-00060813  2022/12/31 00:32:18+00           CFS 459 - Burglary   
48513   2022-00060808  2022/12/31 00:27:58+00        CFS 415 - Disturbance   
48514   2022-00060803  2022/12/31 00:16:42+00     CFS A911 - Ascertain 911   
48515   2022-00060799  2022/12/31 00:15:26+00     CFS A911 - Ascertain 911   
48516   2023-00090006  2022/12/31 00:13:27+00        CFS 487 - Grand Theft   

      Priority                  Block_Address  intersection add_num  \
0      Level 3  SHATTUCK AVE  &  CHANNING WAY          True       0   
1      Level 2                 2400 ASHBY AVE         False    2400   
2      Level 4                    700 PAGE ST         False     700   
3      Level 3                1800 SOLANO AVE         False    1800   
4      Level 2               1300 DELAWARE ST         False    1300   
...        ...                            ...           ...     ...   
48512  Level 3                2200 DWIGHT WAY         False    2200   
48513  Level 4              2000 BERKELEY WAY         False    2000   
48514  Level 1                 2500 MILVIA ST         False    2500   
48515  Level 1                1800 SOLANO AVE         False    1800   
48516   Level                 2600 DWIGHT WAY         False    2600   

            street      street1      street2  alcohol_true_count  \
0              INT  SHATTUCKAVE  CHANNINGWAY                 NaN   
1         ASHBYAVE         NONE         NONE                 4.0   
2           PAGEST         NONE         NONE                 0.0   
3        SOLANOAVE         NONE         NONE                20.0   
4       DELAWAREST         NONE         NONE                 0.0   
...            ...          ...          ...                 ...   
48512    DWIGHTWAY         NONE         NONE                 2.0   
48513  BERKELEYWAY         NONE         NONE                 0.0   
48514     MILVIAST         NONE         NONE                 2.0   
48515    SOLANOAVE         NONE         NONE                20.0   
48516    DWIGHTWAY         NONE         NONE                 2.0   

                                           top_3_busdesc  \
0                                                    NaN   
1      RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
2      ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
3      RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
4      RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
...                                                  ...   
48512  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   
48513  RENTAL PROPERTY, RENTAL RESIDENTIAL 3 UNITS, C...   
48514  RESIDENTIAL RENTAL PROPERTY, COMMERCIAL RENTAL...   
48515  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
48516  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   

                                   top_3_b1_per_sub_type  
0                                                    NaN  
1      Rental of Real Property, Professional SemiProf...  
2      Professional SemiProfessional, Rental of Real ...  
3      Retail Trade, Rental of Real Property, Busines...  
4      Rental of Real Property, Professional SemiProf...  
...                                                  ...  
48512  Rental of Real Property, Professional SemiProf...  
48513  Rental of Real Property, Professional SemiProf...  
48514  Rental of Real Property, Professional SemiProf...  
48515  Retail Trade, Rental of Real Property, Busines...  
48516  Rental of Real Propert

In [74]:
merged_df['CreateDatetime'] = pd.to_datetime(merged_df['CreateDatetime'])

merged_df['Date'] = merged_df['CreateDatetime'].dt.date
merged_df['Time'] = merged_df['CreateDatetime'].dt.time
merged_df['Hour'] = merged_df['CreateDatetime'].dt.hour
merged_df

Incident_Number            CreateDatetime                    Call_Type  \
0       2023-00062204 2023-12-29 20:27:46+00:00        CFS 1182 - Non Injury   
1       2023-00062206 2023-12-29 20:26:14+00:00     CFS 1042 - Welfare Check   
2       2023-00062200 2023-12-29 20:12:38+00:00   CFS FOUND - Found Property   
3       2023-00062228 2023-12-29 20:05:59+00:00  CFS 20002 - Hit & Run Prop.   
4       2023-00062202 2023-12-29 19:45:10+00:00        CFS 415 - Disturbance   
...               ...                       ...                          ...   
48512   2022-00060813 2022-12-31 00:32:18+00:00           CFS 459 - Burglary   
48513   2022-00060808 2022-12-31 00:27:58+00:00        CFS 415 - Disturbance   
48514   2022-00060803 2022-12-31 00:16:42+00:00     CFS A911 - Ascertain 911   
48515   2022-00060799 2022-12-31 00:15:26+00:00     CFS A911 - Ascertain 911   
48516   2023-00090006 2022-12-31 00:13:27+00:00        CFS 487 - Grand Theft   

      Priority                  Block_Address  intersection add_num  \
0      Level 3  SHATTUCK AVE  &  CHANNING WAY          True       0   
1      Level 2                 2400 ASHBY AVE         False    2400   
2      Level 4                    700 PAGE ST         False     700   
3      Level 3                1800 SOLANO AVE         False    1800   
4      Level 2               1300 DELAWARE ST         False    1300   
...        ...                            ...           ...     ...   
48512  Level 3                2200 DWIGHT WAY         False    2200   
48513  Level 4              2000 BERKELEY WAY         False    2000   
48514  Level 1                 2500 MILVIA ST         False    2500   
48515  Level 1                1800 SOLANO AVE         False    1800   
48516   Level                 2600 DWIGHT WAY         False    2600   

            street      street1      street2  alcohol_true_count  \
0              INT  SHATTUCKAVE  CHANNINGWAY                 NaN   
1         ASHBYAVE         NONE         NONE                 4.0   
2           PAGEST         NONE         NONE                 0.0   
3        SOLANOAVE         NONE         NONE                20.0   
4       DELAWAREST         NONE         NONE                 0.0   
...            ...          ...          ...                 ...   
48512    DWIGHTWAY         NONE         NONE                 2.0   
48513  BERKELEYWAY         NONE         NONE                 0.0   
48514     MILVIAST         NONE         NONE                 2.0   
48515    SOLANOAVE         NONE         NONE                20.0   
48516    DWIGHTWAY         NONE         NONE                 2.0   

                                           top_3_busdesc  \
0                                                    NaN   
1      RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
2      ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
3      RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
4      RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
...                                                  ...   
48512  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   
48513  RENTAL PROPERTY, RENTAL RESIDENTIAL 3 UNITS, C...   
48514  RESIDENTIAL RENTAL PROPERTY, COMMERCIAL RENTAL...   
48515  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
48516  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   

                                   top_3_b1_per_sub_type        Date  \
0                                                    NaN  2023-12-29   
1      Rental of Real Property, Professional SemiProf...  2023-12-29   
2      Professional SemiProfessional, Rental of Real ...  2023-12-29   
3      Retail Trade, Rental of Real Property, Busines...  2023-12-29   
4      Rental of Real Property, Professional SemiProf...  2023-12-29   
...                                                  ...         ...   
48512  Rental of Real Property, Professional SemiProf...  2022-12-31   
48513  Rental of Real Property, Professional SemiProf...  2022-12-31   
48514 

In [ ]:
merged_df.to_csv('finalmerge.csv')

In [ ]:
# 시간대별 범죄 많이 일어나는 시간
# 거리별 범죄 많이 일어나는 곳
# 알코올 count가 많은 곳
# 시간대별 특정 범죄가 많이 일어나는지
# 

## final merge 이용 여기서부터!

In [80]:
merged_df = pd.read_csv('finalmerge.csv')
merged_df.head()

Unnamed: 0 Incident_Number             CreateDatetime  \
0           0   2023-00062204  2023-12-29 20:27:46+00:00   
1           1   2023-00062206  2023-12-29 20:26:14+00:00   
2           2   2023-00062200  2023-12-29 20:12:38+00:00   
3           3   2023-00062228  2023-12-29 20:05:59+00:00   
4           4   2023-00062202  2023-12-29 19:45:10+00:00   

                     Call_Type Priority                  Block_Address  \
0        CFS 1182 - Non Injury  Level 3  SHATTUCK AVE  &  CHANNING WAY   
1     CFS 1042 - Welfare Check  Level 2                 2400 ASHBY AVE   
2   CFS FOUND - Found Property  Level 4                    700 PAGE ST   
3  CFS 20002 - Hit & Run Prop.  Level 3                1800 SOLANO AVE   
4        CFS 415 - Disturbance  Level 2               1300 DELAWARE ST   

   intersection  add_num      street      street1      street2  \
0          True        0         INT  SHATTUCKAVE  CHANNINGWAY   
1         False     2400    ASHBYAVE         NONE         NONE   
2         False      700      PAGEST         NONE         NONE   
3         False     1800   SOLANOAVE         NONE         NONE   
4         False     1300  DELAWAREST         NONE         NONE   

   alcohol_true_count                                      top_3_busdesc  \
0                 NaN                                                NaN   
1                 4.0  RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
2                 0.0  ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
3                20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
4                 0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   

                               top_3_b1_per_sub_type        Date      Time  \
0                                                NaN  2023-12-29  20:27:46   
1  Rental of Real Property, Professional SemiProf...  2023-12-29  20:26:14   
2  Professional SemiProfessional, Rental of Real ...  2023-12-29  20:12:38   
3  Retail Trade, Rental of Real Property, Busines...  2023-12-29  20:05:59   
4  Rental of Real Property, Professional SemiProf...  2023-12-29  19:45:10   

   Hour  
0    20  
1    20  
2    20  
3    20  
4    19

In [ ]:
addresses_df = pd.DataFrame()
addresses_df['ID'] = merged_df.index + 1  # ID 열 생성 (1부터 시작)
addresses_df['Street Address'] = merged_df['Block_Address']
addresses_df['City'] = 'Berkeley'  # 고정된 City
addresses_df['State'] = 'CA'  # 고정된 State


ad1=addresses_df[0:10000]
ad2=addresses_df[10000:20000]
ad3=addresses_df[20000:30000]
ad4=addresses_df[30000:40000]
ad5=addresses_df[40000:]

ad1.to_excel("ad1.xlsx", index=False, header=False)
ad2.to_excel("ad2.xlsx", index=False, header=False)
ad3.to_excel("ad3.xlsx", index=False, header=False)
ad4.to_excel("ad4.xlsx", index=False, header=False)
ad5.to_excel("ad5.xlsx", index=False, header=False)

In [ ]:
ad1

In [88]:
import warnings
warnings.filterwarnings("ignore", category=UserWarning, module="openpyxl")

In [90]:
df1 = pd.read_excel('data/ad1.xlsx')
df1 = df1.dropna(subset=['RECORD ID NUMBER'])
df1

RECORD ID NUMBER                                 INPUT ADDRESS  \
1                4970.0                 1200 HENRY ST, Berkeley, CA,    
2                3640.0          1900 LOS ANGELES AVE, Berkeley, CA,    
3                4971.0            1300 SAN PABLO AVE, Berkeley, CA,    
4                2306.0     HOPKINS ST  &  COLUSA AVE, Berkeley, CA,    
5                3638.0      HARMON ST  &  ADELINE ST, Berkeley, CA,    
...                 ...                                           ...   
9996             4955.0               2000 EMERSON ST, Berkeley, CA,    
9997             3628.0               2500 DURANT AVE, Berkeley, CA,    
9998             4956.0             2100 SHATTUCK AVE, Berkeley, CA,    
9999             3627.0  SACRAMENTO ST  &  RUSSELL ST, Berkeley, CA,    
10000            4957.0                   1700 4TH ST, Berkeley, CA,    

      TIGER ADDRESS RANGE MATCH INDICATOR TIGER MATCH TYPE  \
1                                   Match            Exact   
2                                   Match            Exact   
3                                   Match            Exact   
4                                   Match            Exact   
5                                     Tie              NaN   
...                                   ...              ...   
9996                                Match            Exact   
9997                                Match            Exact   
9998                                Match            Exact   
9999                                  Tie              NaN   
10000                            No_Match              NaN   

                               TIGER OUTPUT ADDRESS  \
1                1200 HENRY ST, BERKELEY, CA, 94709   
2         1900 LOS ANGELES AVE, BERKELEY, CA, 94707   
3           1300 SAN PABLO AVE, BERKELEY, CA, 94702   
4      HOPKINS ST & COLUSA AVE, BERKELEY, CA, 94707   
5                                               NaN   
...                                             ...   
9996           2000 EMERSON ST, BERKELEY, CA, 94703   
9997           2500 DURANT AVE, BERKELEY, CA, 94704   
9998         2100 SHATTUCK AVE, BERKELEY, CA, 94704   
9999                                            NaN   
10000                                           NaN   

          INTERPOLATED LONGITUDE AND LATITUDE  TIGERLINE ID TIGERLINE ID SIDE  \
1       -122.27139346400065,37.88536473272654   125080411.0                 R   
2       -122.27669797724644,37.89001068288235   617281585.0                 R   
3        -122.29594986195394,37.8803494403146   124992883.0                 R   
4       -122.27939129321084,37.88292103664054           NaN               NaN   
5                                         NaN           NaN               NaN   
...                                       ...           ...               ...   
9996   -122.26908497842061,37.854153655235564   606280708.0                 R   
9997    -122.25889204512845,37.86778009986563   124998407.0                 R   
9998   -122.26835644132603,37.871114409939025   124994038.0                 R   
9999                                      NaN           NaN               NaN   
10000                                     NaN           NaN               NaN   

       STATE CODE  COUNTY CODE  TRACT CODE  BLOCK CODE  
1             6.0          1.0    421700.0      1005.0  
2             6.0          1.0    421200.0      2019.0  
3             6.0          1.0    422000.0      2014.0  
4             6.0          1.0    421300.0      3009.0  
5             NaN          NaN         NaN         NaN  
...           ...          ...         ...         ...  
9996          6.0          1.0    423901.0      1007.0  
9997          6.0          1.0    422800.0      1002.0  
9998          6.0          1.0    422902.0      3000.0  
9999          NaN          NaN         NaN         NaN  
10000         NaN          NaN         NaN         NaN  

[10000 rows x 12 columns]

In [91]:
df2 = pd.read_excel('data/ad2.xlsx')
df2 = df2.dropna(subset=['RECORD ID NUMBER'])
df3 = pd.read_excel('data/ad3.xlsx')
df3 = df3.dropna(subset=['RECORD ID NUMBER'])
df4 = pd.read_excel('data/ad4.xlsx')
df4 = df4.dropna(subset=['RECORD ID NUMBER'])
df5 = pd.read_excel('data/ad5.xlsx')
df5 = df5.dropna(subset=['RECORD ID NUMBER'])

In [93]:

for _, row in df1.iterrows():
    record_id = row['RECORD ID NUMBER']
    longitude_latitude = row['INTERPOLATED LONGITUDE AND LATITUDE']
    tract_code = row['TRACT CODE']
    block_code = row['BLOCK CODE']
    
    target_index = record_id - 1
    
    if target_index in merged_df.index:
        merged_df.loc[target_index, 'INTERPOLATED LONGITUDE AND LATITUDE'] = longitude_latitude
        merged_df.loc[target_index, 'TRACT CODE'] = tract_code
        merged_df.loc[target_index, 'BLOCK CODE'] = block_code
    else:
        print(f"Index {target_index} not found in merged_df.")

print(merged_df)

       Unnamed: 0 Incident_Number             CreateDatetime  \
0               0   2023-00062204  2023-12-29 20:27:46+00:00   
1               1   2023-00062206  2023-12-29 20:26:14+00:00   
2               2   2023-00062200  2023-12-29 20:12:38+00:00   
3               3   2023-00062228  2023-12-29 20:05:59+00:00   
4               4   2023-00062202  2023-12-29 19:45:10+00:00   
...           ...             ...                        ...   
48512       48512   2022-00060813  2022-12-31 00:32:18+00:00   
48513       48513   2022-00060808  2022-12-31 00:27:58+00:00   
48514       48514   2022-00060803  2022-12-31 00:16:42+00:00   
48515       48515   2022-00060799  2022-12-31 00:15:26+00:00   
48516       48516   2023-00090006  2022-12-31 00:13:27+00:00   

                         Call_Type Priority                  Block_Address  \
0            CFS 1182 - Non Injury  Level 3  SHATTUCK AVE  &  CHANNING WAY   
1         CFS 1042 - Welfare Check  Level 2                 2400 ASHBY AVE 

In [94]:

for _, row in df2.iterrows():
    record_id = row['RECORD ID NUMBER']
    longitude_latitude = row['INTERPOLATED LONGITUDE AND LATITUDE']
    tract_code = row['TRACT CODE']
    block_code = row['BLOCK CODE']
    
    target_index = record_id - 1
    
    if target_index in merged_df.index:
        merged_df.loc[target_index, 'INTERPOLATED LONGITUDE AND LATITUDE'] = longitude_latitude
        merged_df.loc[target_index, 'TRACT CODE'] = tract_code
        merged_df.loc[target_index, 'BLOCK CODE'] = block_code
    else:
        print(f"Index {target_index} not found in merged_df.")
        
for _, row in df3.iterrows():
    record_id = row['RECORD ID NUMBER']
    longitude_latitude = row['INTERPOLATED LONGITUDE AND LATITUDE']
    tract_code = row['TRACT CODE']
    block_code = row['BLOCK CODE']
    
    target_index = record_id - 1
    
    if target_index in merged_df.index:
        merged_df.loc[target_index, 'INTERPOLATED LONGITUDE AND LATITUDE'] = longitude_latitude
        merged_df.loc[target_index, 'TRACT CODE'] = tract_code
        merged_df.loc[target_index, 'BLOCK CODE'] = block_code
    else:
        print(f"Index {target_index} not found in merged_df.")

for _, row in df4.iterrows():
    record_id = row['RECORD ID NUMBER']
    longitude_latitude = row['INTERPOLATED LONGITUDE AND LATITUDE']
    tract_code = row['TRACT CODE']
    block_code = row['BLOCK CODE']
    
    target_index = record_id - 1
    
    if target_index in merged_df.index:
        merged_df.loc[target_index, 'INTERPOLATED LONGITUDE AND LATITUDE'] = longitude_latitude
        merged_df.loc[target_index, 'TRACT CODE'] = tract_code
        merged_df.loc[target_index, 'BLOCK CODE'] = block_code
    else:
        print(f"Index {target_index} not found in merged_df.")

for _, row in df5.iterrows():
    record_id = row['RECORD ID NUMBER']
    longitude_latitude = row['INTERPOLATED LONGITUDE AND LATITUDE']
    tract_code = row['TRACT CODE']
    block_code = row['BLOCK CODE']
    
    target_index = record_id - 1
    
    if target_index in merged_df.index:
        merged_df.loc[target_index, 'INTERPOLATED LONGITUDE AND LATITUDE'] = longitude_latitude
        merged_df.loc[target_index, 'TRACT CODE'] = tract_code
        merged_df.loc[target_index, 'BLOCK CODE'] = block_code
    else:
        print(f"Index {target_index} not found in merged_df.")

In [95]:
merged_df

Unnamed: 0 Incident_Number             CreateDatetime  \
0               0   2023-00062204  2023-12-29 20:27:46+00:00   
1               1   2023-00062206  2023-12-29 20:26:14+00:00   
2               2   2023-00062200  2023-12-29 20:12:38+00:00   
3               3   2023-00062228  2023-12-29 20:05:59+00:00   
4               4   2023-00062202  2023-12-29 19:45:10+00:00   
...           ...             ...                        ...   
48512       48512   2022-00060813  2022-12-31 00:32:18+00:00   
48513       48513   2022-00060808  2022-12-31 00:27:58+00:00   
48514       48514   2022-00060803  2022-12-31 00:16:42+00:00   
48515       48515   2022-00060799  2022-12-31 00:15:26+00:00   
48516       48516   2023-00090006  2022-12-31 00:13:27+00:00   

                         Call_Type Priority                  Block_Address  \
0            CFS 1182 - Non Injury  Level 3  SHATTUCK AVE  &  CHANNING WAY   
1         CFS 1042 - Welfare Check  Level 2                 2400 ASHBY AVE   
2       CFS FOUND - Found Property  Level 4                    700 PAGE ST   
3      CFS 20002 - Hit & Run Prop.  Level 3                1800 SOLANO AVE   
4            CFS 415 - Disturbance  Level 2               1300 DELAWARE ST   
...                            ...      ...                            ...   
48512           CFS 459 - Burglary  Level 3                2200 DWIGHT WAY   
48513        CFS 415 - Disturbance  Level 4              2000 BERKELEY WAY   
48514     CFS A911 - Ascertain 911  Level 1                 2500 MILVIA ST   
48515     CFS A911 - Ascertain 911  Level 1                1800 SOLANO AVE   
48516        CFS 487 - Grand Theft   Level                 2600 DWIGHT WAY   

       intersection  add_num       street      street1      street2  \
0              True        0          INT  SHATTUCKAVE  CHANNINGWAY   
1             False     2400     ASHBYAVE         NONE         NONE   
2             False      700       PAGEST         NONE         NONE   
3             False     1800    SOLANOAVE         NONE         NONE   
4             False     1300   DELAWAREST         NONE         NONE   
...             ...      ...          ...          ...          ...   
48512         False     2200    DWIGHTWAY         NONE         NONE   
48513         False     2000  BERKELEYWAY         NONE         NONE   
48514         False     2500     MILVIAST         NONE         NONE   
48515         False     1800    SOLANOAVE         NONE         NONE   
48516         False     2600    DWIGHTWAY         NONE         NONE   

       alcohol_true_count                                      top_3_busdesc  \
0                     NaN                                                NaN   
1                     4.0  RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
2                     0.0  ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
3                    20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
4                     0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
...                   ...                                                ...   
48512                 2.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   
48513                 0.0  RENTAL PROPERTY, RENTAL RESIDENTIAL 3 UNITS, C...   
48514                 2.0  RESIDENTIAL RENTAL PROPERTY, COMMERCIAL RENTAL...   
48515                20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
48516                 2.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   

                                   top_3_b1_per_sub_type        Date  \
0                                                    NaN  2023-12-29   
1      Rental of Real Property, Professional SemiProf...  2023-12-29   
2      Professional SemiProfessional, Rental of Real ...  2023-12-29   
3      Retail Trade, Rental of Real Property, Busines...  2023-12-29   
4      Rental of Real Property, Professional SemiProf...  2023-12-29   
...                                                  ..

In [132]:
merged_df
merged_df= merged_df.drop(merged_df.columns[0], axis=1)
merged_df.to_csv('data_project.csv')

In [96]:
intersection_df = merged_df[merged_df['intersection'] == True].reset_index(drop=True)
nointersection_df = merged_df[merged_df['intersection'] == False].reset_index(drop=True)

In [112]:
nointersection_df= nointersection_df.drop(nointersection_df.columns[0], axis=1)
nointersection_df.to_csv('nointersection_pd_call.csv')
intersection_df= intersection_df.drop(intersection_df.columns[0], axis=1)
intersection_df.to_csv('intersection_pd_call.csv')

In [114]:
nointersection_df.head()

CreateDatetime                    Call_Type Priority  \
0  2023-12-29 20:26:14+00:00     CFS 1042 - Welfare Check  Level 2   
1  2023-12-29 20:12:38+00:00   CFS FOUND - Found Property  Level 4   
2  2023-12-29 20:05:59+00:00  CFS 20002 - Hit & Run Prop.  Level 3   
3  2023-12-29 19:45:10+00:00        CFS 415 - Disturbance  Level 2   
4  2023-12-29 19:20:23+00:00      CFS 5150 - Mentally Ill  Level 2   

       Block_Address  intersection  add_num       street street1 street2  \
0     2400 ASHBY AVE         False     2400     ASHBYAVE    NONE    NONE   
1        700 PAGE ST         False      700       PAGEST    NONE    NONE   
2    1800 SOLANO AVE         False     1800    SOLANOAVE    NONE    NONE   
3   1300 DELAWARE ST         False     1300   DELAWAREST    NONE    NONE   
4  1400 ALCATRAZ AVE         False     1400  ALCATRAZAVE    NONE    NONE   

   alcohol_true_count                                      top_3_busdesc  \
0                 4.0  RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
1                 0.0  ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
2                20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
3                 0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
4                 2.0         RENTAL PROPERTY, PSYCHOTHERAPY, HAIR SALON   

                               top_3_b1_per_sub_type        Date      Time  \
0  Rental of Real Property, Professional SemiProf...  2023-12-29  20:26:14   
1  Professional SemiProfessional, Rental of Real ...  2023-12-29  20:12:38   
2  Retail Trade, Rental of Real Property, Busines...  2023-12-29  20:05:59   
3  Rental of Real Property, Professional SemiProf...  2023-12-29  19:45:10   
4  Professional SemiProfessional, Rental of Real ...  2023-12-29  19:20:23   

   Hour    INTERPOLATED LONGITUDE AND LATITUDE  TRACT CODE  BLOCK CODE  
0    20  -122.2671275056839,37.855156782900735    423901.0      1001.0  
1    20  -122.30253103597624,37.87591501315046    422000.0      2055.0  
2    20   -122.2802355736689,37.89117554587631    421300.0      4000.0  
3    19   -122.2868943773318,37.87239569978425    422200.0      2003.0  
4    19                                    NaN         NaN         NaN

In [118]:
intersection_nan_count = intersection_df['INTERPOLATED LONGITUDE AND LATITUDE'].isna().sum()
nointersection_nan_count = nointersection_df['INTERPOLATED LONGITUDE AND LATITUDE'].isna().sum()

print("Intersection DataFrame NaN Count for INTERPOLATED LONGITUDE AND LATITUDE:")
print(intersection_nan_count)

print("\nNo Intersection DataFrame NaN Count for INTERPOLATED LONGITUDE AND LATITUDE:")
print(nointersection_nan_count)

Intersection DataFrame NaN Count for INTERPOLATED LONGITUDE AND LATITUDE:
4319

No Intersection DataFrame NaN Count for INTERPOLATED LONGITUDE AND LATITUDE:
3407


In [120]:
nointersection_df = nointersection_df.dropna(subset=['INTERPOLATED LONGITUDE AND LATITUDE']).reset_index(drop=True)
nointersection_df

CreateDatetime                    Call_Type Priority  \
0      2023-12-29 20:26:14+00:00     CFS 1042 - Welfare Check  Level 2   
1      2023-12-29 20:12:38+00:00   CFS FOUND - Found Property  Level 4   
2      2023-12-29 20:05:59+00:00  CFS 20002 - Hit & Run Prop.  Level 3   
3      2023-12-29 19:45:10+00:00        CFS 415 - Disturbance  Level 2   
4      2023-12-29 19:12:30+00:00   CFS BMCVIO - BMC Violation  Level 4   
...                          ...                          ...      ...   
33689  2022-12-31 00:57:10+00:00    CFS 1033A - Audible Alarm  Level 3   
33690  2022-12-31 00:32:18+00:00           CFS 459 - Burglary  Level 3   
33691  2022-12-31 00:27:58+00:00        CFS 415 - Disturbance  Level 4   
33692  2022-12-31 00:15:26+00:00     CFS A911 - Ascertain 911  Level 1   
33693  2022-12-31 00:13:27+00:00        CFS 487 - Grand Theft   Level    

           Block_Address  intersection  add_num       street street1 street2  \
0         2400 ASHBY AVE         False     2400     ASHBYAVE    NONE    NONE   
1            700 PAGE ST         False      700       PAGEST    NONE    NONE   
2        1800 SOLANO AVE         False     1800    SOLANOAVE    NONE    NONE   
3       1300 DELAWARE ST         False     1300   DELAWAREST    NONE    NONE   
4      1200 FRANCISCO ST         False     1200  FRANCISCOST    NONE    NONE   
...                  ...           ...      ...          ...     ...     ...   
33689        1900 6TH ST         False     1900      SIXTHST    NONE    NONE   
33690    2200 DWIGHT WAY         False     2200    DWIGHTWAY    NONE    NONE   
33691  2000 BERKELEY WAY         False     2000  BERKELEYWAY    NONE    NONE   
33692    1800 SOLANO AVE         False     1800    SOLANOAVE    NONE    NONE   
33693    2600 DWIGHT WAY         False     2600    DWIGHTWAY    NONE    NONE   

       alcohol_true_count                                      top_3_busdesc  \
0                     4.0  RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
1                     0.0  ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
2                    20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
3                     0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
4                     0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   
...                   ...                                                ...   
33689                 2.0  COMMERCIAL RENTAL PROPERTY, RENTAL PROPERTY/3 ...   
33690                 2.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   
33691                 0.0  RENTAL PROPERTY, RENTAL RESIDENTIAL 3 UNITS, C...   
33692                20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
33693                 2.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   

                                   top_3_b1_per_sub_type        Date  \
0      Rental of Real Property, Professional SemiProf...  2023-12-29   
1      Professional SemiProfessional, Rental of Real ...  2023-12-29   
2      Retail Trade, Rental of Real Property, Busines...  2023-12-29   
3      Rental of Real Property, Professional SemiProf...  2023-12-29   
4      Rental of Real Property, Professional SemiProf...  2023-12-29   
...                                                  ...         ...   
33689  Rental of Real Property, Professional SemiProf...  2022-12-31   
33690  Rental of Real Property, Professional SemiProf...  2022-12-31   
33691  Rental of Real Property, Professional SemiProf...  2022-12-31   
33692  Retail Trade, Rental of Real Property, Busines...  2022-12-31   
33693  Rental of Real Property, Professional SemiProf...  2022-12-31   

           Time  Hour    INTERPOLATED LONGITUDE AND LATITUDE  TRACT CODE  \
0      20:26:14    20  -122.2671275056839,37.855156782900735    423901.0   
1      20:12:38    20  -122.30253103597624,37.87591501315046    422000.0   
2      20:05:59    20   -122.2802355736689,37.89117554587631    421300.0   
3      19:45:10    19   -122.286894377

In [124]:
nointersection_df.head()

CreateDatetime                    Call_Type Priority  \
0  2023-12-29 20:26:14+00:00     CFS 1042 - Welfare Check  Level 2   
1  2023-12-29 20:12:38+00:00   CFS FOUND - Found Property  Level 4   
2  2023-12-29 20:05:59+00:00  CFS 20002 - Hit & Run Prop.  Level 3   
3  2023-12-29 19:45:10+00:00        CFS 415 - Disturbance  Level 2   
4  2023-12-29 19:12:30+00:00   CFS BMCVIO - BMC Violation  Level 4   

       Block_Address  intersection  add_num       street street1 street2  \
0     2400 ASHBY AVE         False     2400     ASHBYAVE    NONE    NONE   
1        700 PAGE ST         False      700       PAGEST    NONE    NONE   
2    1800 SOLANO AVE         False     1800    SOLANOAVE    NONE    NONE   
3   1300 DELAWARE ST         False     1300   DELAWAREST    NONE    NONE   
4  1200 FRANCISCO ST         False     1200  FRANCISCOST    NONE    NONE   

   alcohol_true_count                                      top_3_busdesc  \
0                 4.0  RENTAL PROPERTY, COMMERCIAL RENTAL PROPERTY, P...   
1                 0.0  ART STUDIO CERAMICS INSTRUCTION, PROPERTY MANA...   
2                20.0  RESTAURANT, HAIR SALON, COMMERCIAL RENTAL PROP...   
3                 0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL 5 UNITS, R...   
4                 0.0  RENTAL PROPERTY, RESIDENTIAL RENTAL PROPERTY, ...   

                               top_3_b1_per_sub_type        Date      Time  \
0  Rental of Real Property, Professional SemiProf...  2023-12-29  20:26:14   
1  Professional SemiProfessional, Rental of Real ...  2023-12-29  20:12:38   
2  Retail Trade, Rental of Real Property, Busines...  2023-12-29  20:05:59   
3  Rental of Real Property, Professional SemiProf...  2023-12-29  19:45:10   
4  Rental of Real Property, Professional SemiProf...  2023-12-29  19:12:30   

   Hour    INTERPOLATED LONGITUDE AND LATITUDE  TRACT CODE  BLOCK CODE  
0    20  -122.2671275056839,37.855156782900735    423901.0      1001.0  
1    20  -122.30253103597624,37.87591501315046    422000.0      2055.0  
2    20   -122.2802355736689,37.89117554587631    421300.0      4000.0  
3    19   -122.2868943773318,37.87239569978425    422200.0      2003.0  
4    19  -122.28985189352238,37.87297325325261    422200.0      3005.0

In [126]:
nointersection_df = nointersection_df.drop(columns=['street1', 'street2'])

# 결과 확인
print(nointersection_df.head())

              CreateDatetime                    Call_Type Priority  \
0  2023-12-29 20:26:14+00:00     CFS 1042 - Welfare Check  Level 2   
1  2023-12-29 20:12:38+00:00   CFS FOUND - Found Property  Level 4   
2  2023-12-29 20:05:59+00:00  CFS 20002 - Hit & Run Prop.  Level 3   
3  2023-12-29 19:45:10+00:00        CFS 415 - Disturbance  Level 2   
4  2023-12-29 19:12:30+00:00   CFS BMCVIO - BMC Violation  Level 4   

       Block_Address  intersection  add_num       street  alcohol_true_count  \
0     2400 ASHBY AVE         False     2400     ASHBYAVE                 4.0   
1        700 PAGE ST         False      700       PAGEST                 0.0   
2    1800 SOLANO AVE         False     1800    SOLANOAVE                20.0   
3   1300 DELAWARE ST         False     1300   DELAWAREST                 0.0   
4  1200 FRANCISCO ST         False     1200  FRANCISCOST                 0.0   

                                       top_3_busdesc  \
0  RENTAL PROPERTY, COMMERCIAL RENTAL PROP

In [128]:
nointersection_df.to_csv('df.csv')

In [122]:
nointersection_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33694 entries, 0 to 33693
Data columns (total 18 columns):
 #   Column                               Non-Null Count  Dtype  
---  ------                               --------------  -----  
 0   CreateDatetime                       33694 non-null  object 
 1   Call_Type                            33694 non-null  object 
 2   Priority                             33694 non-null  object 
 3   Block_Address                        33694 non-null  object 
 4   intersection                         33694 non-null  bool   
 5   add_num                              33694 non-null  int64  
 6   street                               33694 non-null  object 
 7   street1                              33694 non-null  object 
 8   street2                              33694 non-null  object 
 9   alcohol_true_count                   33694 non-null  float64
 10  top_3_busdesc                        33694 non-null  object 
 11  top_3_b1_per_sub_type       

In [516]:
locations = []
values = []

for index, row in nointersection_df.iterrows():
    lon_lat = row['INTERPOLATED LONGITUDE AND LATITUDE'].split(',')
    lon = float(lon_lat[0])
    lat = float(lon_lat[1])
    alcohol_count = row['alcohol_true_count']
    
    locations.append([lat, lon, alcohol_count])

map_center = [nointersection_df['INTERPOLATED LONGITUDE AND LATITUDE'].apply(lambda x: float(x.split(',')[1])).mean(), 
              nointersection_df['INTERPOLATED LONGITUDE AND LATITUDE'].apply(lambda x: float(x.split(',')[0])).mean()]

m = folium.Map(location=map_center, zoom_start=14)

HeatMap(locations, radius=10, blur=15).add_to(m)
m

In [518]:
locations = []

for index, row in nointersection_df.iterrows():
    lon_lat = row['INTERPOLATED LONGITUDE AND LATITUDE'].split(',')
    lon = float(lon_lat[0])
    lat = float(lon_lat[1])
    
    locations.append([lat, lon])

map_center = [sum([loc[0] for loc in locations]) / len(locations),
              sum([loc[1] for loc in locations]) / len(locations)]

m = folium.Map(location=map_center, zoom_start=14)

heat_data = [[loc[0], loc[1]] for loc in locations]

HeatMap(heat_data, min_opacity=0.2, radius=15, blur=10).add_to(m)
m

In [522]:
locations_with_count = []
for index, row in nointersection_df.iterrows():
    lon_lat = row['INTERPOLATED LONGITUDE AND LATITUDE'].split(',')
    lon = float(lon_lat[0])
    lat = float(lon_lat[1])
    alcohol_count = row['alcohol_true_count']
    locations_with_count.append([lat, lon, alcohol_count])

locations_without_count = []
for index, row in nointersection_df.iterrows():
    lon_lat = row['INTERPOLATED LONGITUDE AND LATITUDE'].split(',')
    lon = float(lon_lat[0])
    lat = float(lon_lat[1])
    locations_without_count.append([lat, lon])

map_center = [sum([loc[0] for loc in locations_without_count]) / len(locations_without_count),
              sum([loc[1] for loc in locations_without_count]) / len(locations_without_count)]

m = folium.Map(location=map_center, zoom_start=14)

HeatMap(locations_with_count, radius=15, blur=10, min_opacity=0.2).add_to(m)

HeatMap(locations_without_count, radius=15, blur=10, min_opacity=0.2, gradient={0: 'blue', 0.5: 'yellow', 1: 'red'}).add_to(m)
m

In [526]:
from scipy.stats import pearsonr
df_with_count = pd.DataFrame({
    'latitude': [float(loc[0]) for loc in locations_with_count],
    'longitude': [float(loc[1]) for loc in locations_with_count],
    'alcohol_count': [loc[2] for loc in locations_with_count]
})

df_without_count = pd.DataFrame({
    'latitude': [float(loc[0]) for loc in locations_without_count],
    'longitude': [float(loc[1]) for loc in locations_without_count]
})

count_with_count = df_with_count.groupby(['latitude', 'longitude']).sum().reset_index()
count_without_count = df_without_count.groupby(['latitude', 'longitude']).size().reset_index(name='data_count')

merged_df = pd.merge(count_with_count, count_without_count, on=['latitude', 'longitude'], how='inner')

correlation, _ = pearsonr(merged_df['alcohol_count'], merged_df['data_count'])
print(f'Correlation coefficient: {correlation}')

Correlation coefficient: 0.7207334778953762


In [528]:
locations_with_count = [[float(loc[0]), float(loc[1]), loc[2]] for loc in locations_with_count]
locations_without_count = [[float(loc[0]), float(loc[1])] for loc in locations_without_count]

map_center = [np.mean([float(loc[0]) for loc in locations_with_count]), 
              np.mean([float(loc[1]) for loc in locations_with_count])]

m = folium.Map(location=map_center, zoom_start=14)

HeatMap([[loc[0], loc[1], loc[2]] for loc in locations_with_count], radius=15, blur=10, gradient={0: 'blue', 0.5: 'yellow', 1: 'red'}).add_to(m)
HeatMap([[loc[0], loc[1]] for loc in locations_without_count], radius=15, blur=10, gradient={0: 'blue', 0.5: 'yellow', 1: 'red'}).add_to(m)

m